In [225]:
import pandas as pd
import pyodbc
import numpy as np
from datetime import datetime
from dateutil.relativedelta import relativedelta
from dateutil.rrule import rrule, MONTHLY
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import cross_val_score
import plotly.express as px
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from tqdm import tqdm
from scipy.optimize import minimize
from scipy.optimize import curve_fit
from scipy.stats import halfnorm
import shap
import numdifftools as nd
from hyperopt import tpe, hp, fmin, STATUS_OK,Trials
from hyperopt.pyll.base import scope
import pickle
from tqdm import tqdm
shap.initjs()
%load_ext autoreload
%autoreload 2
import mmm_transformations
import mmm_preprocessing
import mmm_modeling
import mmm_response_curves
import mmm_optimization

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# Preprocessing

In [207]:
df_pp = pd.read_csv('sim_data_r (1).csv')
df_pp['date'] = pd.to_datetime(df_pp['date'])
df_pp.drop(['Unnamed: 0'], axis=1, inplace=True)
df_pp = pd.concat([df_pp, pd.get_dummies(df_pp[['Specialty']])], axis=1)
df_pp

Specialty       date  rx_count  Email  Phone  Digital  \
0     Neurologist 2020-09-15       199    185    523       44   
1     Neurologist 2020-09-22       167      3    910      446   
2     Neurologist 2020-09-29       212     81    864      147   
3     Neurologist 2020-10-06       214    141    998      131   
4     Neurologist 2020-10-13       214     38    888      427   
..            ...        ...       ...    ...    ...      ...   
355  Hematologist 2022-11-29       219     30    590      234   
356  Hematologist 2022-12-06       206     20    287      422   
357  Hematologist 2022-12-13        99    182    934        2   
358  Hematologist 2022-12-20       251    174    808      410   
359  Hematologist 2022-12-27       200     17    246      337   

     Specialty_Hematologist  Specialty_Neurologist  Specialty_Oncologist  
0                         0                      1                     0  
1                         0                      1                     0  
2                         0                      1                     0  
3                         0                      1                     0  
4                         0                      1                     0  
..                      ...                    ...                   ...  
355                       1                      0                     0  
356                       1                      0                     0  
357                       1                      0                     0  
358                       1                      0                     0  
359                       1                      0                     0  

[360 rows x 9 columns]

In [224]:
df_pp[df_pp['Specialty']=='Neurologist'].to_csv('sim_data_r_neurologist.csv', index=False)

# Transformations

In [208]:
transform = mmm_transformations.MMMTransformations()

In [209]:
df_t = transform.lag_dv(df_pp, 'rx_count', 3, 'Specialty')
df_t = transform.lag_dv(df_t, 'Email', 3, 'Specialty')
df_t = transform.lag_dv(df_t, 'Phone', 3, 'Specialty')
df_t = transform.lag_dv(df_t, 'Digital', 3, 'Specialty')
df_t

Specialty       date  rx_count  Email  Phone  Digital  \
0     Neurologist 2020-09-15       199    185    523       44   
1     Neurologist 2020-09-22       167      3    910      446   
2     Neurologist 2020-09-29       212     81    864      147   
3     Neurologist 2020-10-06       214    141    998      131   
4     Neurologist 2020-10-13       214     38    888      427   
..            ...        ...       ...    ...    ...      ...   
355  Hematologist 2022-11-29       219     30    590      234   
356  Hematologist 2022-12-06       206     20    287      422   
357  Hematologist 2022-12-13        99    182    934        2   
358  Hematologist 2022-12-20       251    174    808      410   
359  Hematologist 2022-12-27       200     17    246      337   

     Specialty_Hematologist  Specialty_Neurologist  Specialty_Oncologist  \
0                         0                      1                     0   
1                         0                      1                     0   
2                         0                      1                     0   
3                         0                      1                     0   
4                         0                      1                     0   
..                      ...                    ...                   ...   
355                       1                      0                     0   
356                       1                      0                     0   
357                       1                      0                     0   
358                       1                      0                     0   
359                       1                      0                     0   

     rx_count_lag1  ...  rx_count_lag3  Email_lag1  Email_lag2  Email_lag3  \
0                0  ...              0           0           0           0   
1              199  ...              0         185           0           0   
2              167  ...              0           3         185           0   
3              212  ...            199          81           3         185   
4              214  ...            167         141          81           3   
..             ...  ...            ...         ...         ...         ...   
355            212  ...            245           9          71         102   
356            219  ...            202          30           9          71   
357            206  ...            212          20          30           9   
358             99  ...            219         182          20          30   
359            251  ...            206         174         182          20   

     Phone_lag1  Phone_lag2  Phone_lag3  Digital_lag1  Digital_lag2  \
0             0           0           0             0             0   
1           523           0           0            44             0   
2           910         523           0           446            44   
3           864         910         523           147           446   
4           998         864         910           131           147   
..          ...         ...         ...           ...           ...   
355         741         239         577           438            59   
356         590         741         239           234           438   
357         287         590         741           422           234   
358         934         287         590             2           422   
359         808         934         287           410             2   

     Digital_lag3  
0               0  
1               0  
2               0  
3              44  
4             446  
..            ...  
355           274  
356            59  
357           438  
358           234  
359           422  

[360 rows x 21 columns]

In [210]:
df_t.describe()

rx_count       Email       Phone     Digital  Specialty_Hematologist  \
count  360.000000  360.000000  360.000000  360.000000              360.000000   
mean   184.566667   95.791667  525.305556  256.455556                0.333333   
std     41.707444   58.012999  284.562531  139.537490                0.472061   
min     50.000000    0.000000    7.000000    1.000000                0.000000   
25%    155.750000   47.000000  293.500000  139.750000                0.000000   
50%    194.500000   95.000000  528.000000  263.500000                0.000000   
75%    217.000000  146.250000  776.000000  372.000000                1.000000   
max    252.000000  200.000000  999.000000  496.000000                1.000000   

       Specialty_Neurologist  Specialty_Oncologist  rx_count_lag1  \
count             360.000000            360.000000     360.000000   
mean                0.333333              0.333333     183.069444   
std                 0.472061              0.472061      44.798380   
min                 0.000000              0.000000       0.000000   
25%                 0.000000              0.000000     155.000000   
50%                 0.000000              0.000000     193.000000   
75%                 1.000000              1.000000     217.000000   
max                 1.000000              1.000000     252.000000   

       rx_count_lag2  rx_count_lag3  Email_lag1  Email_lag2  Email_lag3  \
count     360.000000     360.000000  360.000000  360.000000  360.000000   
mean      181.369444     180.277778   95.316667   94.300000   93.647222   
std        47.615740      50.152476   58.493147   58.641577   58.839288   
min         0.000000       0.000000    0.000000    0.000000    0.000000   
25%       154.750000     154.750000   46.500000   43.750000   43.000000   
50%       192.000000     192.000000   95.000000   94.500000   93.500000   
75%       217.000000     217.000000  146.250000  144.500000  143.250000   
max       252.000000     252.000000  200.000000  200.000000  200.000000   

       Phone_lag1  Phone_lag2  Phone_lag3  Digital_lag1  Digital_lag2  \
count  360.000000  360.000000  360.000000    360.000000    360.000000   
mean   521.122222  514.875000  510.358333    254.358333    252.591667   
std    287.036877  290.002898  292.253147    141.135040    142.322567   
min      0.000000    0.000000    0.000000      0.000000      0.000000   
25%    286.250000  279.500000  272.750000    137.750000    135.500000   
50%    527.500000  522.000000  513.000000    259.500000    258.500000   
75%    769.500000  761.250000  759.250000    372.000000    371.000000   
max    999.000000  999.000000  999.000000    496.000000    496.000000   

       Digital_lag3  
count    360.000000  
mean     250.600000  
std      143.267212  
min        0.000000  
25%      132.500000  
50%      256.500000  
75%      370.250000  
max      496.000000

In [211]:
spec_cols = ['Specialty_Hematologist', 'Specialty_Neurologist', 'Specialty_Oncologist']
df_t_n = df_t[df_t['Specialty']=='Neurologist'].drop(spec_cols, axis=1)
df_t_o = df_t[df_t['Specialty']=='Oncologist'].drop(spec_cols, axis=1)
df_t_h = df_t[df_t['Specialty']=='Hematologist'].drop(spec_cols, axis=1)

In [212]:
df_t_n

Specialty       date  rx_count  Email  Phone  Digital  rx_count_lag1  \
0    Neurologist 2020-09-15       199    185    523       44              0   
1    Neurologist 2020-09-22       167      3    910      446            199   
2    Neurologist 2020-09-29       212     81    864      147            167   
3    Neurologist 2020-10-06       214    141    998      131            212   
4    Neurologist 2020-10-13       214     38    888      427            214   
..           ...        ...       ...    ...    ...      ...            ...   
115  Neurologist 2022-11-29       193     15    561      209            138   
116  Neurologist 2022-12-06       218    113    883      282            193   
117  Neurologist 2022-12-13       141     52    140      422            218   
118  Neurologist 2022-12-20       207    181    831       50            141   
119  Neurologist 2022-12-27       218     92    957      318            207   

     rx_count_lag2  rx_count_lag3  Email_lag1  Email_lag2  Email_lag3  \
0                0              0           0           0           0   
1                0              0         185           0           0   
2              199              0           3         185           0   
3              167            199          81           3         185   
4              212            167         141          81           3   
..             ...            ...         ...         ...         ...   
115            146            204         106          61          31   
116            138            146          15         106          61   
117            193            138         113          15         106   
118            218            193          52         113          15   
119            141            218         181          52         113   

     Phone_lag1  Phone_lag2  Phone_lag3  Digital_lag1  Digital_lag2  \
0             0           0           0             0             0   
1           523           0           0            44             0   
2           910         523           0           446            44   
3           864         910         523           147           446   
4           998         864         910           131           147   
..          ...         ...         ...           ...           ...   
115           7         208         687           238           130   
116         561           7         208           209           238   
117         883         561           7           282           209   
118         140         883         561           422           282   
119         831         140         883            50           422   

     Digital_lag3  
0               0  
1               0  
2               0  
3              44  
4             446  
..            ...  
115           164  
116           130  
117           238  
118           209  
119           282  

[120 rows x 18 columns]

In [28]:
fig = px.scatter(df_t_n, x="Email", y='rx_count')
fig.show()

# Model Fitting

In [216]:
modeling = mmm_modeling.MMMModeling()

In [217]:
# modeling
channels = ['Email', 'Phone', 'Digital']
lag_dv = [x for x in df_t.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t[channels + lag_channels + lag_dv]
y = df_t['rx_count']
model_n = modeling.rf_regressor(df_t_n, X.columns.tolist(), 'rx_count', 'date')
model_o = modeling.rf_regressor(df_t_o, X.columns.tolist(), 'rx_count', 'date')
model_h = modeling.rf_regressor(df_t_h, X.columns.tolist(), 'rx_count', 'date')

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_modeling.py:56: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_modeling.py:57: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_modeling.py:56: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instea

In [239]:
# performance
model_n['performance']

{'full': {'r2': 0.9838121680217206,
  'rmse': 3.981616924483486,
  'mape': 0.015527005524675603},
 'train': {'r2': 0.982884671854277,
  'rmse': 4.01163931579099,
  'mape': 0.01641592564915347},
 'test': {'r2': 0.8932231988217967,
  'rmse': 10.643472765033039,
  'mape': 0.04898760405829511}}

In [168]:
model_o['performance']

{'full': {'r2': 0.9900485235036529,
  'rmse': 1.863273329385681,
  'mape': 0.008071327616117686},
 'train': {'r2': 0.9847938740885716,
  'rmse': 2.37396907449669,
  'mape': 0.009570789817775876},
 'test': {'r2': 0.9577957465054455,
  'rmse': 3.2020299550961946,
  'mape': 0.014289380927799066}}

In [169]:
model_h['performance']

{'full': {'r2': 0.9921224103148366,
  'rmse': 3.2228645384709136,
  'mape': 0.013223172412832985},
 'train': {'r2': 0.9922676779966322,
  'rmse': 3.4487955325011677,
  'mape': 0.014988580470816845},
 'test': {'r2': 0.845869767130621,
  'rmse': 6.927184071949198,
  'mape': 0.02080326812178428}}

In [170]:
# importance
model_n['importance']

feature  importance       std
1           Phone    0.769578  0.063648
0           Email    0.149949  0.074380
2         Digital    0.020805  0.022570
8      Phone_lag3    0.009289  0.026890
7      Phone_lag2    0.008141  0.021636
11   Digital_lag3    0.007337  0.011915
13  rx_count_lag2    0.007184  0.019488
10   Digital_lag2    0.005209  0.018167
9    Digital_lag1    0.004585  0.009972
5      Email_lag3    0.004197  0.017107
6      Phone_lag1    0.003960  0.009989
4      Email_lag2    0.003268  0.004687
14  rx_count_lag3    0.002379  0.005423
12  rx_count_lag1    0.002131  0.005169
3      Email_lag1    0.001986  0.003691

In [171]:
model_o['importance']

feature  importance       std
2         Digital    0.565278  0.099521
1           Phone    0.362547  0.114927
11   Digital_lag3    0.010461  0.020132
5      Email_lag3    0.009993  0.011996
6      Phone_lag1    0.008098  0.017259
8      Phone_lag3    0.007511  0.017044
7      Phone_lag2    0.005875  0.012795
13  rx_count_lag2    0.005539  0.015510
9    Digital_lag1    0.005231  0.014549
12  rx_count_lag1    0.004111  0.009282
14  rx_count_lag3    0.004073  0.013435
0           Email    0.003686  0.007144
3      Email_lag1    0.003247  0.010055
4      Email_lag2    0.002701  0.007502
10   Digital_lag2    0.001649  0.005613

In [172]:
model_h['importance']

feature  importance       std
2         Digital    0.758521  0.087368
0           Email    0.098471  0.045650
1           Phone    0.074208  0.033777
13  rx_count_lag2    0.019197  0.035173
11   Digital_lag3    0.009895  0.027907
10   Digital_lag2    0.007232  0.020925
8      Phone_lag3    0.005321  0.013914
4      Email_lag2    0.005194  0.011500
9    Digital_lag1    0.004802  0.014213
7      Phone_lag2    0.004409  0.016321
6      Phone_lag1    0.003569  0.006755
5      Email_lag3    0.003179  0.008439
3      Email_lag1    0.002637  0.005031
14  rx_count_lag3    0.001829  0.005042
12  rx_count_lag1    0.001536  0.003137

In [188]:
model_n['df_preds_test']

Specialty       date  rx_count  Email  Phone  Digital  rx_count_lag1  \
0    Neurologist  9/15/2020       199    185    523       44              0   
1    Neurologist  9/22/2020       167      3    910      446            199   
2    Neurologist  9/29/2020       212     81    864      147            167   
42   Neurologist   7/6/2021       215     80    638      363            173   
45   Neurologist  7/27/2021       218    200    684      325            137   
46   Neurologist   8/3/2021       142    156    122      306            218   
47   Neurologist  8/10/2021       217     58    883      430            142   
48   Neurologist  8/17/2021       213     37    830      370            217   
49   Neurologist  8/24/2021        50      0    160      401            213   
50   Neurologist  8/31/2021       139     83     15      352             50   
51   Neurologist   9/7/2021       217    112    734      295            139   
52   Neurologist  9/14/2021       159     22    341       24            217   
53   Neurologist  9/21/2021       208     43    717      166            159   
54   Neurologist  9/28/2021       217    190    612      369            208   
94   Neurologist   7/5/2022       213     95    659      219            197   
98   Neurologist   8/2/2022       218    101    700      381            219   
99   Neurologist   8/9/2022       104    115     67        1            218   
100  Neurologist  8/16/2022       191     10    564      480            104   
101  Neurologist  8/23/2022       131     43    168       71            191   
102  Neurologist  8/30/2022       210    192    469      353            131   
103  Neurologist   9/6/2022       189    186    342      227            210   
104  Neurologist  9/13/2022       214     82    572      404            189   
105  Neurologist  9/20/2022       188     19    441      179            214   
106  Neurologist  9/27/2022       175     12    482       51            188   

     rx_count_lag2  rx_count_lag3  Email_lag1  Email_lag2  Email_lag3  \
0                0              0           0           0           0   
1                0              0         185           0           0   
2              199              0           3         185           0   
42             213            179          11          73          16   
45             128            215          80          18          80   
46             137            128         200          80          18   
47             218            137         156         200          80   
48             142            218          58         156         200   
49             217            142          37          58         156   
50             213            217           0          37          58   
51              50            213          83           0          37   
52             139             50         112          83           0   
53             217            139          22         112          83   
54             159            217          43          22         112   
94             200            209          74          34          60   
98             212            199         180         131          32   
99             219            212         101         180         131   
100            218            219         115         101         180   
101            104            218          10         115         101   
102            191            104          43          10         115   
103            131            191         192          43          10   
104            210            131         186         192          43   
105            189            210          82         186         192   
106            214            189          19          82         186   

     Phone_lag1  Phone_lag2  Phone_lag3  Digital_lag1  Digital_lag2  \
0             0           0           0             0             0   
1           523           0           0            44          

In [196]:
# scatter plot of predictions
plot_df = pd.DataFrame({'date': model_n['df_preds_full']['date'], 'preds': model_n['df_preds_full']['preds_full'],
                        'actual': model_n['df_preds_full']['rx_count']})
fig = px.scatter(plot_df, x="date", y=plot_df.columns.tolist(), title="Full Data - Model trained on full data")
fig.show()

In [197]:
# scatter plot of predictions
plot_df = pd.DataFrame({'date': model_n['df_preds_test']['date'].astype(str),
                        'preds': model_n['df_preds_test']['preds_test'],
                        'actual': model_n['df_preds_test']['rx_count']})
fig = px.scatter(plot_df, x="date", y=plot_df.columns.tolist(), title="Future Hold Out Set")
fig.show()

# Response Curves - Neurologist

In [303]:
response_curves = mmm_response_curves.MMMResponseCurves()

In [304]:
channels = ['Email', 'Phone', 'Digital']
lag_dv = [x for x in df_t_n.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t_n.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t_n[channels + lag_channels + lag_dv]
#X[channels + lag_channels] = 0

In [233]:
df_t_n.describe()

rx_count       Email       Phone     Digital  rx_count_lag1  \
count  120.000000  120.000000  120.000000  120.000000     120.000000   
mean   191.475000   93.758333  553.983333  267.875000     189.658333   
std     31.425505   60.272908  269.328046  133.429902      35.866582   
min     50.000000    0.000000    7.000000    1.000000       0.000000   
25%    177.250000   43.000000  372.500000  165.500000     175.000000   
50%    203.000000   83.500000  541.000000  283.500000     202.500000   
75%    214.000000  148.500000  791.500000  380.250000     214.000000   
max    221.000000  200.000000  998.000000  493.000000     221.000000   

       rx_count_lag2  rx_count_lag3  Email_lag1  Email_lag2  Email_lag3  \
count     120.000000     120.000000  120.000000  120.000000  120.000000   
mean      187.933333     186.758333   92.991667   91.483333   91.050000   
std        39.788883      43.128301   60.877546   60.920941   61.387302   
min         0.000000       0.000000    0.000000    0.000000    0.000000   
25%       174.500000     174.500000   41.750000   37.750000   36.500000   
50%       201.500000     201.500000   83.000000   82.500000   82.500000   
75%       214.000000     214.000000  148.500000  142.750000  142.750000   
max       221.000000     221.000000  200.000000  200.000000  200.000000   

       Phone_lag1  Phone_lag2  Phone_lag3  Digital_lag1  Digital_lag2  \
count  120.000000  120.000000  120.000000    120.000000    120.000000   
mean   546.008333  539.083333  537.916667    265.225000    264.808333   
std    271.454486  274.703311  276.702479    135.566751    136.308615   
min      0.000000    0.000000    0.000000      0.000000      0.000000   
25%    358.000000  345.500000  345.500000    159.750000    159.750000   
50%    538.000000  532.500000  532.500000    281.500000    281.500000   
75%    785.750000  782.500000  782.500000    380.250000    380.250000   
max    998.000000  998.000000  998.000000    493.000000    493.000000   

       Digital_lag3  
count    120.000000  
mean     261.291667  
std      137.656093  
min        0.000000  
25%      145.500000  
50%      275.000000  
75%      377.750000  
max      493.000000

In [305]:
# overall response curves
channel1_n = response_curves.responses(model_n['full_model'], X, 'Email', 200, 1)
channel2_n = response_curves.responses(model_n['full_model'], X, 'Phone', 1000, 10)
channel3_n = response_curves.responses(model_n['full_model'], X, 'Digital', 500, 5)

 49%|██████████████████████████████████████████████████████████████████████████████████████████▋                                                                                               | 98/201 [00:02<00:03, 28.99it/s]D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh

 59%|████████████████████████████████████████████████████████████████████████████████████████████████████████████▌                                                                            | 118/201 [00:03<00:02, 32.19it/s]D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

 70%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊                                                        | 140/201 [00:04<00:01, 38.32it/s]D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performan

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

 89%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊                    | 179/201 [00:05<00:00, 35.23it/s]D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh

 99%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏ | 199/201 [00:05<00:00, 38.84it/s]D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:139: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

100%|█████████████

In [306]:
response_curves.plot(channel1_n['resp_df'], 'touches', ['Email', 'Email_hill_estimate'])

In [307]:
response_curves.plot(channel2_n['resp_df'], 'touches', ['Phone', 'Phone_hill_estimate'])

In [308]:
response_curves.plot(channel3_n['resp_df'], 'touches', ['Digital', 'Digital_hill_estimate'])

In [81]:
channel3['resp_df'].to_csv('D:/Users/hartsingh/Documents/Projects/Misc output/digital_n.csv', index=False)

# Response Curves - Oncologist

In [44]:
channels = ['Email', 'Phone', 'Digital']
lag_dv = [x for x in df_t_o.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t_o.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t_o[channels + lag_channels + lag_dv]
#X[channels + lag_channels] = 0

In [45]:
df_t_o.describe()

date    rx_count       Email       Phone     Digital  \
count  120.000000  120.000000  120.000000  120.000000  120.000000   
mean    60.500000  145.858333   97.616667  505.566667  259.591667   
std     34.785054   18.756420   57.008356  280.657354  137.129424   
min      1.000000   83.000000    1.000000    7.000000    3.000000   
25%     30.750000  137.000000   52.500000  278.250000  143.000000   
50%     60.500000  154.500000   94.500000  534.000000  254.500000   
75%     90.250000  160.000000  146.000000  729.250000  363.250000   
max    120.000000  163.000000  199.000000  999.000000  496.000000   

       rx_count_lag1  rx_count_lag2  rx_count_lag3  Email_lag1  Email_lag2  \
count     120.000000     120.000000     120.000000  120.000000  120.000000   
mean      144.850000     143.566667     142.291667   97.100000   97.008333   
std        22.898993      26.425648      29.481057   57.611623   57.758334   
min         0.000000       0.000000       0.000000    0.000000    0.000000   
25%       137.000000     134.000000     133.500000   50.750000   50.750000   
50%       154.500000     154.500000     154.500000   94.500000   94.500000   
75%       160.000000     160.000000     160.000000  146.000000  146.000000   
max       163.000000     163.000000     163.000000  199.000000  199.000000   

       Email_lag3  Phone_lag1  Phone_lag2  Phone_lag3  Digital_lag1  \
count  120.000000  120.000000  120.000000  120.000000    120.000000   
mean    97.000000  503.041667  497.958333  493.358333    258.758333   
std     57.772373  283.840066  287.349037  290.873353    138.405323   
min      0.000000    0.000000    0.000000    0.000000      0.000000   
25%     50.750000  270.500000  257.250000  236.500000    143.000000   
50%     94.500000  534.000000  522.500000  504.500000    254.500000   
75%    146.000000  729.250000  729.250000  729.250000    363.250000   
max    199.000000  999.000000  999.000000  999.000000    496.000000   

       Digital_lag2  Digital_lag3  
count    120.000000    120.000000  
mean     257.291667    254.850000  
std      140.210430    142.121539  
min        0.000000      0.000000  
25%      142.750000    141.250000  
50%      254.500000    251.000000  
75%      363.250000    363.250000  
max      496.000000    496.000000

In [46]:
# overall response curves
channel1_o = response_curves.responses(model_o['full_model'], X, 'Email', 200, 1)
channel2_o = response_curves.responses(model_o['full_model'], X, 'Phone', 1000, 10)
channel3_o = response_curves.responses(model_o['full_model'], X, 'Digital', 500, 5)

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:22: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_cur

In [47]:
response_curves.plot(channel1_o['resp_df'], 'touches', ['Email', 'Email_hill_estimate'])

In [48]:
response_curves.plot(channel2_o['resp_df'], 'touches', ['Phone', 'Phone_hill_estimate'])

In [49]:
response_curves.plot(channel3_o['resp_df'], 'touches', ['Digital', 'Digital_hill_estimate'])

In [65]:
channel3['resp_df'].to_csv('D:/Users/hartsingh/Documents/Projects/Misc output/digital_o.csv', index=False)

# Response Curves - Hematologist

In [50]:
channels = ['Email', 'Phone', 'Digital']
lag_dv = [x for x in df_t_h.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t_h.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t_o[channels + lag_channels + lag_dv]
#X[channels + lag_channels] = 0

In [51]:
df_t_h.describe()

date    rx_count       Email       Phone     Digital  \
count  120.000000  120.000000  120.000000  120.000000  120.000000   
mean    60.500000  216.366667   96.000000  516.366667  241.900000   
std     34.785054   36.463850   57.120395  302.786219  147.567925   
min      1.000000   58.000000    1.000000   23.000000    1.000000   
25%     30.750000  209.000000   45.750000  258.000000  119.500000   
50%     60.500000  225.500000  101.000000  504.500000  253.000000   
75%     90.250000  242.000000  144.750000  798.250000  370.250000   
max    120.000000  252.000000  198.000000  995.000000  493.000000   

       rx_count_lag1  rx_count_lag2  rx_count_lag3  Email_lag1  Email_lag2  \
count     120.000000     120.000000     120.000000  120.000000  120.000000   
mean      214.700000     212.608333     211.783333   95.858333   94.408333   
std        41.448277      45.714734      48.585398   57.338637   57.545670   
min         0.000000       0.000000       0.000000    0.000000    0.000000   
25%       209.000000     208.750000     208.750000   45.750000   41.750000   
50%       225.500000     224.000000     224.000000  101.000000  100.500000   
75%       242.000000     241.250000     241.250000  144.750000  143.250000   
max       252.000000     252.000000     252.000000  198.000000  198.000000   

       Email_lag3  Phone_lag1  Phone_lag2  Phone_lag3  Digital_lag1  \
count  120.000000  120.000000  120.000000  120.000000    120.000000   
mean    92.891667  514.316667  507.583333  499.800000    239.091667   
std     57.616057  305.453128  307.821338  308.755474    148.943168   
min      0.000000    0.000000    0.000000    0.000000      0.000000   
25%     40.500000  258.000000  251.000000  237.250000    115.500000   
50%     99.000000  504.500000  494.500000  487.000000    250.000000   
75%    143.000000  798.250000  795.750000  790.500000    370.250000   
max    198.000000  995.000000  995.000000  995.000000    493.000000   

       Digital_lag2  Digital_lag3  
count     120.00000    120.000000  
mean      235.67500    235.658333  
std       149.69039    149.716735  
min         0.00000      0.000000  
25%       106.50000    106.500000  
50%       248.00000    248.000000  
75%       368.50000    368.500000  
max       493.00000    493.000000

In [52]:
# overall response curves
channel1_h = response_curves.responses(model_h['full_model'], X, 'Email', 200, 1)
channel2_h = response_curves.responses(model_h['full_model'], X, 'Phone', 1000, 10)
channel3_h = response_curves.responses(model_h['full_model'], X, 'Digital', 500, 5)

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:90: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:22: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_cur

In [53]:
response_curves.plot(channel1_h['resp_df'], 'touches', ['Email', 'Email_hill_estimate'])

In [54]:
response_curves.plot(channel2_h['resp_df'], 'touches', ['Phone', 'Phone_hill_estimate'])

In [55]:
response_curves.plot(channel3_h['resp_df'], 'touches', ['Digital', 'Digital_hill_estimate'])

In [151]:
channel3['optimal_hill']

array([130.93790319,  29.24294816,   1.74773258])

In [90]:
channel3['resp_df'].to_csv('D:/Users/hartsingh/Documents/Projects/Misc output/digital_h.csv', index=False)

# Neurologist Optimization - Hyperopt 

In [60]:
neuro_hill = pd.concat([pd.DataFrame(channel1_n['optimal_hill']).T,
                          pd.DataFrame(channel2_n['optimal_hill']).T,
                          pd.DataFrame(channel3_n['optimal_hill']).T])
neuro_hill.columns = ['beta', 'gamma', 'alpha']
neuro_hill['feature'] = ['Email', 'Phone', 'Digital']
neuro_hill

beta       gamma     alpha  feature
0  46.633193   11.928508  2.026613    Email
0  79.256993  309.583473  4.311753    Phone
0   6.444855  118.903393  2.624504  Digital

In [62]:
df_t_n.describe()

date    rx_count       Email       Phone     Digital  \
count  120.000000  120.000000  120.000000  120.000000  120.000000   
mean    60.500000  191.475000   93.758333  553.983333  267.875000   
std     34.785054   31.425505   60.272908  269.328046  133.429902   
min      1.000000   50.000000    0.000000    7.000000    1.000000   
25%     30.750000  177.250000   43.000000  372.500000  165.500000   
50%     60.500000  203.000000   83.500000  541.000000  283.500000   
75%     90.250000  214.000000  148.500000  791.500000  380.250000   
max    120.000000  221.000000  200.000000  998.000000  493.000000   

       rx_count_lag1  rx_count_lag2  rx_count_lag3  Email_lag1  Email_lag2  \
count     120.000000     120.000000     120.000000  120.000000  120.000000   
mean      189.658333     187.933333     186.758333   92.991667   91.483333   
std        35.866582      39.788883      43.128301   60.877546   60.920941   
min         0.000000       0.000000       0.000000    0.000000    0.000000   
25%       175.000000     174.500000     174.500000   41.750000   37.750000   
50%       202.500000     201.500000     201.500000   83.000000   82.500000   
75%       214.000000     214.000000     214.000000  148.500000  142.750000   
max       221.000000     221.000000     221.000000  200.000000  200.000000   

       Email_lag3  Phone_lag1  Phone_lag2  Phone_lag3  Digital_lag1  \
count  120.000000  120.000000  120.000000  120.000000    120.000000   
mean    91.050000  546.008333  539.083333  537.916667    265.225000   
std     61.387302  271.454486  274.703311  276.702479    135.566751   
min      0.000000    0.000000    0.000000    0.000000      0.000000   
25%     36.500000  358.000000  345.500000  345.500000    159.750000   
50%     82.500000  538.000000  532.500000  532.500000    281.500000   
75%    142.750000  785.750000  782.500000  782.500000    380.250000   
max    200.000000  998.000000  998.000000  998.000000    493.000000   

       Digital_lag2  Digital_lag3  
count    120.000000    120.000000  
mean     264.808333    261.291667  
std      136.308615    137.656093  
min        0.000000      0.000000  
25%      159.750000    145.500000  
50%      281.500000    275.000000  
75%      380.250000    377.750000  
max      493.000000    493.000000

In [63]:
# current impact
optimization = mmm_optimization.MMMOptimization(budget=750, params=neuro_hill)
imp = optimization.calc_impact([94, 554, 268])
imp

{'impact': 124.99056931920633, 'total spend': 916}

In [125]:
# optimized spend using hill - no interactions
optimization = mmm_optimization.MMMOptimization(budget=916, params=neuro_hill)
channels = neuro_hill['feature'].tolist()
output = optimization.optimize_hyperopt_hill(channels, 2000)
output

100%|███████████████████████████████████████████████████████████████████████████████████████████████| 2000/2000 [00:39<00:00, 50.21trial/s, best loss: -125.53066810514927]


{'mix': {'Digital': 109, 'Email': 71, 'Phone': 716},
 'total_spend': 896,
 'trials': [{'loss': -69.45087711833435, 'status': 'ok'},
  {'loss': 99999892.9695586, 'status': 'ok'},
  {'loss': 99999903.20732604, 'status': 'ok'},
  {'loss': 99999897.355319, 'status': 'ok'},
  {'loss': 99999875.84125774, 'status': 'ok'},
  {'loss': 99999872.74446605, 'status': 'ok'},
  {'loss': 99999945.98180272, 'status': 'ok'},
  {'loss': 99999922.20143571, 'status': 'ok'},
  {'loss': 99999872.7862767, 'status': 'ok'},
  {'loss': 99999869.84834781, 'status': 'ok'},
  {'loss': 99999903.51472604, 'status': 'ok'},
  {'loss': -51.05912090328378, 'status': 'ok'},
  {'loss': 99999868.57149981, 'status': 'ok'},
  {'loss': 99999879.40974009, 'status': 'ok'},
  {'loss': -52.953479447788936, 'status': 'ok'},
  {'loss': 99999874.88649186, 'status': 'ok'},
  {'loss': 99999943.53318813, 'status': 'ok'},
  {'loss': 99999886.3019586, 'status': 'ok'},
  {'loss': 99999871.29883143, 'status': 'ok'},
  {'loss': 99999871.0216

In [126]:
# optimized spend using model - includes interactions
optimization = mmm_optimization.MMMOptimization(budget=916)
lag_dv = [x for x in df_t_n.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t_n.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t_n[channels + lag_channels + lag_dv]
output = optimization.optimize_predict(X, channels, 2000, model_n['full_model'], 1)
output

100%|███████████████████████████████████████████████████████████████████████████████████████████████| 2000/2000 [01:14<00:00, 26.79trial/s, best loss: -115.33233333333334]


{'mix': {'Digital': 141, 'Email': 105, 'Phone': 614},
 'total_spend': 860,
 'baseline_impact': 95.91383333333333,
 'trials': [{'loss': 99999885.56125, 'status': 'ok'},
  {'loss': 99999958.86708333, 'status': 'ok'},
  {'loss': 99999890.81458333, 'status': 'ok'},
  {'loss': -39.85841666666667, 'status': 'ok'},
  {'loss': 99999964.33708334, 'status': 'ok'},
  {'loss': -73.36733333333333, 'status': 'ok'},
  {'loss': 99999936.43583333, 'status': 'ok'},
  {'loss': -30.460083333333337, 'status': 'ok'},
  {'loss': 99999889.55241667, 'status': 'ok'},
  {'loss': 99999965.07875, 'status': 'ok'},
  {'loss': 99999906.06475, 'status': 'ok'},
  {'loss': 99999915.706, 'status': 'ok'},
  {'loss': -74.47175, 'status': 'ok'},
  {'loss': 99999889.17875, 'status': 'ok'},
  {'loss': 99999945.39466667, 'status': 'ok'},
  {'loss': 99999888.051, 'status': 'ok'},
  {'loss': 99999929.965, 'status': 'ok'},
  {'loss': 99999898.54125, 'status': 'ok'},
  {'loss': -32.688750000000006, 'status': 'ok'},
  {'loss': 9999

In [113]:
channels

['Email', 'Phone', 'Digital']

In [118]:
optimization.calc_impact_model(X, channels, model_n['full_model'], [94, 554, 268])

{'impact': 113.43233333333335, 'total spend': 916}

In [127]:
optimization.calc_impact_model(X, channels, model_n['full_model'], [71, 716, 109])

{'impact': 111.90316666666668, 'total spend': 896}

In [109]:
channel3_n['resp_og']

touches     Digital
0          0  186.527167
1          5  186.747833
2         10  186.927167
3         15  187.127417
4         20  187.127417
..       ...         ...
96       480  191.813917
97       485  191.770917
98       490  191.480167
99       495  191.480167
100      500  191.480167

[101 rows x 2 columns]

In [110]:
channel3_n['resp_df']

touches   Digital  Digital_hill_estimate  touches_scaled  \
0        0.0  0.000000               0.000000            0.00   
1        5.0  0.220667               0.001575            0.01   
2       10.0  0.400000               0.009699            0.02   
3       15.0  0.600250               0.028030            0.03   
4       20.0  0.600250               0.059347            0.04   
..       ...       ...                    ...             ...   
96     480.0  5.286750               6.283556            0.96   
97     485.0  5.243750               6.287778            0.97   
98     490.0  4.953000               6.291851            0.98   
99     495.0  4.953000               6.295781            0.99   
100    500.0  4.953000               6.299574            1.00   

     Digital_hill_estimate_minmax  
0                        0.000000  
1                        0.000250  
2                        0.001540  
3                        0.004449  
4                        0.009421  
..                            ...  
96                       0.997457  
97                       0.998127  
98                       0.998774  
99                       0.999398  
100                      1.000000  

[101 rows x 5 columns]

# Digital Optimization - Hill

In [56]:
df_plot = pd.DataFrame({'touches': channel3_n['resp_df']['touches'],
                        'digital_n': channel3_n['resp_df']['Digital_hill_estimate'],
                        'digital_o': channel3_o['resp_df']['Digital_hill_estimate'],
                        'digital_h': channel3_h['resp_df']['Digital_hill_estimate']})
response_curves.plot(df_plot, 'touches', ['digital_n', 'digital_o', 'digital_h'])

In [178]:
digital_hill = pd.concat([pd.DataFrame(channel3_n['optimal_hill']).T,
                          pd.DataFrame(channel3_o['optimal_hill']).T,
                          pd.DataFrame(channel3_h['optimal_hill']).T])
digital_hill['segment'] = ['N', 'O', 'H']
digital_hill.columns = ['beta', 'gamma', 'alpha', 'feature']
digital_hill

beta       gamma     alpha feature
0    7.921299   91.412755  1.870447       N
0   42.530765  125.371314  7.450854       O
0  130.937903   29.242948  1.747733       H

In [191]:
optimization = mmm_optimization.MMMOptimization(budget=769, params=digital_hill)
start_vals = [100, 100, 100]
output = optimization.optimize_hill(start_vals)
output

-1*((7.921298838162023*(1/(1+(n[0]/91.41275456254392)**(-1.8704470641254065))))+(42.53076461169334*(1/(1+(n[1]/125.3713138983588)**(-7.450853709127819))))+(130.93790319195642*(1/(1+(n[2]/29.242948164898635)**(-1.7477325774874637)))))
[207.46509906 239.6287677  321.90613325]
     fun: -177.69590060953857
     jac: array([-0.01042938, -0.01042938, -0.01042938])
 message: 'Optimization terminated successfully'
    nfev: 117
     nit: 29
    njev: 29
  status: 0
 success: True
       x: array([207.46509906, 239.6287677 , 321.90613325])


In [199]:
# optimal 1 - use all budget
imp = optimization.calc_impact([207.46509906, 239.6287677 , 321.90613325])
imp

{'impact': 177.69590060964285, 'total spend': 769.0000000099999}

In [204]:
# optimal 2 - saver
imp = optimization.calc_impact([200, 200, 200])
imp

{'impact': 174.2370212725674, 'total spend': 600}

In [200]:
# current
imp = optimization.calc_impact([267.875000, 259.591667, 241.900000])
imp

{'impact': 177.08637224154015, 'total spend': 769.3666669999999}

# Bootstrap Prediction Intervals

In [291]:
response_curves = mmm_response_curves.MMMResponseCurves()
channels = ['Email', 'Phone', 'Digital']
lag_dv = [x for x in df_t_n.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t_n.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t_n[channels + lag_channels + lag_dv]
y = df_t_n['rx_count']

channel1_n_errors = response_curves.responses(model_n['full_model'], X, 'Email', 200, 1, y=y, samples=50)

 66%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍                                                               | 33/50 [00:07<00:04,  4.06it/s]


 32%|███████████████████████████████████████████████████████████▊                                                                                                                               | 16/50 [00:03<00:08,  4.20it/s]


  1%|█▊                                                                                                                                                                                         | 2/201 [00:24<41:43, 12.58s/it]


 68%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏                                                           | 34/50 [00:08<00:03,  4.41it/s]


 34%|███████████████████████████████████████████████████████████████▌                                                                                                                           | 17/50 [00:05<00:09,  3.44it/s]


...

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:15<00:00,  3.17it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

 99%|████████████

 80%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌                                     | 40/50 [00:10<00:02,  4.30it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:13<00:00,  3.73it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

100%|████████████

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:14<00:00,  3.53it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`



100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 201/201 [45:44<00:00, 13.65s/it]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:24: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:24: RuntimeWarning:

divide by zero encountered in power



In [295]:
channel1_n['resp_og']

touches       Email
0          0  150.386000
1          1  150.386000
2          2  150.386000
3          3  154.954583
4          4  154.954583
..       ...         ...
196      196  196.641417
197      197  196.641417
198      198  196.641417
199      199  196.666833
200      200  196.666833

[201 rows x 2 columns]

In [292]:
channel1_n_errors['resp_og']

touches       Email  Email_errors
0          0  150.386000     23.950926
1          1  150.386000     24.413824
2          2  150.386000     25.036575
3          3  154.954583     23.808678
4          4  154.954583     24.227431
..       ...         ...           ...
196      196  196.641417     24.312339
197      197  196.641417     25.426978
198      198  196.641417     23.315703
199      199  196.666833     22.790567
200      200  196.666833     24.880898

[201 rows x 3 columns]

In [317]:
np.mean(channel1_n_errors['resp_og']['Email_errors']/channel1_n_errors['resp_og']['Email'])

0.12626519818792722

In [294]:
fig = go.Figure(data=go.Scatter(x=channel1_n_errors['resp_og']['touches'], y=channel1_n_errors['resp_og']['Email'],
                                error_y=dict(type='data', array=channel1_n_errors['resp_og']['Email_errors'], visible=True)))
fig.show()

In [296]:
response_curves = mmm_response_curves.MMMResponseCurves()
channels = ['Email', 'Phone', 'Digital']
lag_dv = [x for x in df_t_n.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t_n.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t_n[channels + lag_channels + lag_dv]
y = df_t_n['rx_count']

channel2_n_errors = response_curves.responses(model_n['full_model'], X, 'Phone', 1000, 10, y=y, samples=50)

fig = go.Figure(data=go.Scatter(x=channel2_n_errors['resp_og']['touches'], y=channel2_n_errors['resp_og']['Phone'],
                                error_y=dict(type='data', array=channel2_n_errors['resp_og']['Phone_errors'], visible=True)))
fig.show()

 66%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍                                                               | 33/50 [00:09<00:05,  3.12it/s]


 32%|███████████████████████████████████████████████████████████▊                                                                                                                               | 16/50 [00:06<00:15,  2.21it/s]


  2%|███▋                                                                                                                                                                                       | 2/101 [00:35<29:50, 18.08s/it]


 68%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏                                                           | 34/50 [00:10<00:05,  3.04it/s]


 34%|███████████████████████████████████████████████████████████████▌                                                                                                                           | 17/50 [00:05<00:10,  3.09it/s]


...

 90%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▎                  | 45/50 [00:13<00:01,  3.28it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:14<00:00,  3.36it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

 98%|████████████

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:13<00:00,  3.70it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

 99%|████████████

 72%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▋                                                    | 36/50 [00:10<00:03,  3.73it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:14<00:00,  3.40it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

100%|████████████

In [309]:
channel2_n['resp_og']

touches       Phone
0          0  131.085167
1         10  131.081583
2         20  131.106583
3         30  131.138000
4         40  131.300250
..       ...         ...
96       960  209.383833
97       970  209.383833
98       980  209.368833
99       990  209.443333
100     1000  209.434000

[101 rows x 2 columns]

In [298]:
channel2_n_errors['resp_og']

touches       Phone  Phone_errors
0          0  131.085167     42.107238
1         10  131.081583     42.375527
2         20  131.106583     41.303412
3         30  131.138000     40.044584
4         40  131.300250     42.178398
..       ...         ...           ...
96       960  209.383833     41.687569
97       970  209.383833     40.940872
98       980  209.368833     41.955049
99       990  209.443333     41.666629
100     1000  209.434000     42.637191

[101 rows x 3 columns]

In [318]:
np.mean(channel2_n_errors['resp_og']['Phone_errors']/channel2_n_errors['resp_og']['Phone'])

0.23319537525786216

In [297]:
fig = go.Figure(data=go.Scatter(x=channel2_n_errors['resp_og']['touches'], y=channel2_n_errors['resp_og']['Phone'],
                                error_y=dict(type='data', array=channel2_n_errors['resp_og']['Phone_errors'], visible=True)))
fig.show()

In [313]:
response_curves = mmm_response_curves.MMMResponseCurves()
channels = ['Email', 'Phone', 'Digital']
lag_dv = [x for x in df_t_n.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t_n.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t_n[channels + lag_channels + lag_dv]
y = df_t_n['rx_count']

channel3_n_errors = response_curves.responses(model_n['full_model'], X, 'Digital', 500, 5, y=y, samples=50)

 66%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍                                                               | 33/50 [00:10<00:04,  3.60it/s]


 32%|███████████████████████████████████████████████████████████▊                                                                                                                               | 16/50 [00:05<00:13,  2.61it/s]


  2%|███▋                                                                                                                                                                                       | 2/101 [00:33<27:45, 16.82s/it]


 68%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏                                                           | 34/50 [00:11<00:04,  3.55it/s]


 34%|███████████████████████████████████████████████████████████████▌                                                                                                                           | 17/50 [00:05<00:10,  3.18it/s]


...

 90%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▎                  | 45/50 [00:12<00:01,  3.57it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:13<00:00,  3.66it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

 98%|████████████

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:14<00:00,  3.48it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

 99%|████████████

 72%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▋                                                    | 36/50 [00:10<00:04,  3.32it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [00:14<00:00,  3.55it/s]
D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:142: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\promotional_response_rf\research\mmm_response_curves.py:143: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

100%|████████████

In [314]:
channel3_n['resp_og']

touches     Digital
0          0  186.671167
1          5  187.308833
2         10  187.308833
3         15  187.317000
4         20  187.317000
..       ...         ...
96       480  191.894167
97       485  191.853000
98       490  191.579750
99       495  191.579750
100      500  191.579750

[101 rows x 2 columns]

In [315]:
channel3_n_errors['resp_og']

touches     Digital  Digital_errors
0          0  186.671167       18.805752
1          5  187.308833       18.771907
2         10  187.308833       19.223267
3         15  187.317000       19.718956
4         20  187.317000       18.572170
..       ...         ...             ...
96       480  191.894167       18.099591
97       485  191.853000       18.601169
98       490  191.579750       19.022758
99       495  191.579750       18.854742
100      500  191.579750       19.733898

[101 rows x 3 columns]

In [319]:
np.mean(channel3_n_errors['resp_og']['Digital_errors']/channel3_n_errors['resp_og']['Digital'])

0.10046966356562007

In [316]:
fig = go.Figure(data=go.Scatter(x=channel3_n_errors['resp_og']['touches'], y=channel3_n_errors['resp_og']['Digital'],
                                error_y=dict(type='data', array=channel3_n_errors['resp_og']['Digital_errors'], visible=True)))
fig.show()

In [320]:
response_curves = mmm_response_curves.MMMResponseCurves()
channels = ['Email', 'Phone', 'Digital']
lag_dv = [x for x in df_t_n.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t_n.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t_n[channels + lag_channels + lag_dv]
y = df_t_n['rx_count']
prediction_intervals = response_curves.prediction_interval(X, y)
print(prediction_intervals)
#response_curves.error_propagation(prediction_intervals)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 100/100 [00:30<00:00,  3.26it/s]

[[197.8965  206.301  ]
 [156.0055  201.3575 ]
 [208.798   212.321  ]
 [207.5295  213.9115 ]
 [204.37225 214.86075]
 [217.64125 220.96   ]
 [195.758   204.62275]
 [143.691   182.77125]
 [198.60225 209.00525]
 [187.8555  201.6225 ]
 [186.556   204.43375]
 [197.08525 204.752  ]
 [213.0985  217.08675]
 [210.525   216.75575]
 [174.9895  189.53175]
 [185.91475 199.63475]
 [186.14325 203.411  ]
 [188.78625 201.466  ]
 [195.1745  203.808  ]
 [152.1455  176.172  ]
 [202.4655  209.0035 ]
 [167.3285  191.8775 ]
 [212.96775 217.061  ]
 [193.285   204.6825 ]
 [198.822   209.91575]
 [194.29125 203.89625]
 [206.9465  211.08825]
 [195.13375 208.77825]
 [149.5785  179.629  ]
 [187.1935  200.18275]
 [127.1305  152.73125]
 [148.66575 179.80025]
 [207.93025 213.14775]
 [216.41925 219.93525]
 [214.62425 217.70975]
 [202.942   207.704  ]
 [188.02825 204.8835 ]
 [203.3355  213.03925]
 [216.34125 218.952  ]
 [178.43725 195.8775 ]
 [210.4325  213.9515 ]
 [166.94275 186.091  ]
 [213.31375 216.0315 ]
 [106.807  

In [ ]:
# fit a model for each simulation
# dont need an error bar for each data point maybe every 10 or 20 points
# try lowess in R - give confidence intervals and use reticulate to merge python and r